<h1><center>COVID-19 Product Notebook</center></h1>
<h3><center>Authors: Cynthia Mather, Sherry Wang, Johnson Yun, Hendrix Wang and Charles Zhang</center></h3>
<h4><center>Abstract: The coranvirus pandemic that has put the world on hold, has infected the lives of many people and taken away lives too. We have seen different countries being impacted at different rates and dealing with it differently which has result in an uncertainty of how deadly this virus is. This product notebook aims to explain clearly how deadly this virus is for six countries with uncertainties that are explained for our wide audience, from the general public to researches. The key finding in this notebook is the high death rate given by the infection fatality rate (as a percentage) is low for all countries in contrast to what is viewed in the media as it accounts for individuals that have contracted the virus but go unreported. Australia currently having the highest death rate and and India having the lowest has lead to an outburst of cognitive bias present in the think alouds when key visualisations were viewed by five participants. </center></h4> 



## **A. Introduction**


### A.1. Purpose and Driving Question

*The author of this section is: Sherry*

*The editor of this section is: Cynthia*

*start 5-11-2020 end 17-11-2020*

This notebook is aimed to explore the driving question about **how deadly is COVID-19**. Also exploring ways to **analyse and present the uncertainties visually in a meaningful way**. For the purpose of this notebook we will focus on six countries including Australia, Brazil, India, Russia, South Africa and United States. (The countries are chosen from different continents so that it provides a holistic, unbiased analysis.)

### A.2. Data Source

#### A.2.1. Overview of key explorations in this notebook

Key explorations in this file include: 

**Exploratory Data analysis** to find the trends and patterns in key variables namely `new_smoothed_cases`, `new_smoothed_deaths`, `new_smoothed_testing` and `total_recovered`. Additionally, the relationships and correlations between multiple variables are also explored.

**Case Fatality Rate analysis** to compare Case Fatality Rate across the six countries and determine the underlyting patterns.

**Infection Fatality Rate analysis** of the countries and coupled with the uncertainties associated with the models' estimation of infection cases. These results are also presented in graphs to gain visual insights.

**Uncertainties presentation** explores the factors of uncertainties that contribute quantitatively in addressing the driving question, "How deadly is COVID-19" and to visualise the results in a more meaningful manner for the audience. 


#### A.2.2. Details on Dataset


In total, there are six different datasets that are imported for the data analysis. The main dataset used in this notebook is sourced from ['Our World in Data'](https://ourworldindata.org/coronavirus). And the supplementary data is from ['John Hopkins University'](https://coronavirus.jhu.edu/map.html) specifically to obtain the numbers of recovered cases for each country. Both data sources are updated daily and retrieved directly from the institution's Github link. Both datasets includes COVID data for Australia, Brazil, India, Russia, South Africa and United States, which is suitable for this notebook's purpose. It is important to highlight that since these raw data is sourced directly from the Github link that is managed by the two organisations, hence both raw data have been *preserved immutability*.

The 5 other datasets are sourced from ['Our World in Data'](https://ourworldindata.org/covid-models) which is data of the epidemiological models for COVID-19 that allows us to choose the most appropriate model to estimate the infected cases in each country. Since we would like to estimate the number of true infection cases in order to precisely obtain the death rate of COVID-19. It is also important to note that these model datasets have not been preserved thier immutability as we would like them to, since they require downloads. However, to minimise the risk of mutating the raw data files we download and re-upload the data on our group Github with the file untouched.


##  **B. Analysis**

### B.1. Data Engineering

*The author of this section is: Sherry Wang*

*The editor of this section is: Cynthia Mather*

*start 8-11-2020 end 18-11-2020*

This section will include importing all libraries; reading in all data used for analysis; identify and dealing with missing data and explaining reasons why; reformatting and transforming datasets and the underlying reasons; merging muiltiple datasets, identify outliers and explain how we dealt with them. The data engineering section is to ensure the appropriateness and valuable of the datasets for further analysis.

#### Import Libraries

The code below imports essential packages in order to conduct analysis. To ensure reproducibility, the versions for the libraries above are commented asside each package. 

In [1]:
import plotly# 4.11.0
import sklearn# 0.20.1
import pandas as pd # 1.1.3
import numpy as np # 1.15.4
import plotly.express as px # 4.11.0
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from math import log10, floor
from sklearn.linear_model import LinearRegression # 0.20.1
from IPython.display import Markdown as md
pd.options.mode.chained_assignment = None 

In [2]:
libraries={"pandas":pd,"numpy":np, "plotly":plotly,"sklearn":sklearn}
for key in libraries.keys():
    print("The version for {} is {}".format(key,libraries.get(key).__version__))

The version for pandas is 1.1.3
The version for numpy is 1.15.4
The version for plotly is 4.11.0
The version for sklearn is 0.20.1


All required libraies and packages are installed in the section above. Now we can continue with reading in all the raw data that will be used in the following analysis.

#### Load Datasets

We need to load in our data to begin the analysis. The code below reads in the global COVID-19 data from the "Our World in Data" source straight from the GitHub repository to ensure the most updated version is being used in this analysis as updates are made daily.

In [3]:
df=pd.read_csv("https://raw.githubusercontent.com/owid/covid-19-data/master/public/data/owid-covid-data.csv")

The file sourced from "Our World in Data" is read into this notebook as `df` as it is the main dataset that our analysis is based on.

Same step is done to load in the "John Hopkins" dataset, to complement the missing variable `recovered` cases in the "Our World in Data" we would like to explore.

In [4]:
jh_recovered=pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')

The data has been loaded in the cell above. John Hopkins data for recovered cases is named as `jh_recovered`.

Next we will load in the dataset for the estimations of the infection cases of 4 different models, this is for the purpose of exploring the different models.

In [5]:
estimate_raw=pd.read_csv('https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/Process%20Notebooks/Checkpoint%202/Model%20Datasets/daily-new-estimated-infections-of-covid-19.csv?token=AAABCGD5VDINVEXSYDV3LCK7XWLYY')

The dataset for all 4 models' estimation is loaded in as above and assigned to `estimate_raw`.

The following line will load in the data for each models (detailed data consisting the model's upper and lower bound for estimations) that we will be using for calculating the Infection Fatality Rates.

In [6]:
icl_raw=pd.read_csv('https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/Process%20Notebooks/Checkpoint%202/Model%20Datasets/daily-new-estimated-covid-19-infections-icl-model.csv?token=AAABCGHB7KD5WCEDJ73CMSK7XWL4Q')
ihme_raw=pd.read_csv('https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/Process%20Notebooks/Checkpoint%202/Model%20Datasets/daily-new-estimated-covid-19-infections-ihme-model.csv?token=AAABCGFYRPI74VJCZGTVMES7XWL5U')
yyg_raw=pd.read_csv('https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/Process%20Notebooks/Checkpoint%202/Model%20Datasets/daily-new-estimated-covid-19-infections-yyg-model.csv?token=AAABCGELR7KXYA3NW2VT4XS7XWL7G')
lshtm_raw=pd.read_csv('https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/Process%20Notebooks/Checkpoint%202/Model%20Datasets/daily-new-estimated-covid-19-infections-lshtm-model.csv?token=AAABCGHPPF432BVBMREVRS27XWL6S')

All 4 model datasets are loaded in separately and each named after their model name, including `icl_raw`,`ihme_raw`, `yyg_raw` and `lshtm_raw`.

#### Data Munging

First we will go through the process of data munging to transform into another data format to make it appropriate for data analysis. Ideally, we would like to work with only one dataset as this makes data wrangling and exploration easier than working on two separate datasets, hence `jh_recovered` is transformed so that it can merge with `df`.

We print out the first five rows for `jh_recovered` dataset.

In [7]:
jh_recovered.head()

Province/State Country/Region       Lat       Long  1/22/20  1/23/20  \
0            NaN    Afghanistan  33.93911  67.709953        0        0   
1            NaN        Albania  41.15330  20.168300        0        0   
2            NaN        Algeria  28.03390   1.659600        0        0   
3            NaN        Andorra  42.50630   1.521800        0        0   
4            NaN         Angola -11.20270  17.873900        0        0   

   1/24/20  1/25/20  1/26/20  1/27/20  ...  11/7/20  11/8/20  11/9/20  \
0        0        0        0        0  ...    34446    34458    34721   
1        0        0        0        0  ...    12002    12092    12203   
2        0        0        0        0  ...    41783    42037    42325   
3        0        0        0        0  ...     4043     4248     4332   
4        0        0        0        0  ...     5647     5899     5927   

   11/10/20  11/11/20  11/12/20  11/13/20  11/14/20  11/15/20  11/16/20  
0     34954     34967     35024     35036     35067     35092     35137  
1     12353     12493     12574     12667     12767     12889     13453  
2     42626     42980     42980     43779     44199     44633     45148  
3      4405      4488      4585      4675      4675      4747      4830  
4      6036      6125      6250      6326      6345      6444      6523  

[5 rows x 304 columns]

From the output above we can observe that the John Hopkin's dataset has split the dates into separte columns, hence we need to transform the dataframe from wide to long format using the melt function so that the dataframe is consistent with the Our World in data or `df`, suitable for later analysis.

In [8]:
jh_recovered2=jh_recovered.melt(id_vars=['Province/State','Country/Region','Lat','Long'],
                                var_name = 'date', 
                                value_name = 'total_recovered')
jh_recovered2.head()

Province/State Country/Region       Lat       Long     date  total_recovered
0            NaN    Afghanistan  33.93911  67.709953  1/22/20                0
1            NaN        Albania  41.15330  20.168300  1/22/20                0
2            NaN        Algeria  28.03390   1.659600  1/22/20                0
3            NaN        Andorra  42.50630   1.521800  1/22/20                0
4            NaN         Angola -11.20270  17.873900  1/22/20                0

In the above code we reformatted the John Hopkin's file by melting the data under multiple columns into a new column called `total_recovered` that records the recovered cases for each day and is grouped by the countries. Simultaneously, a new column `date` is added. This new dataframe is named after `jh_recovered2` as printed in the output above. The new dataframe has only six columns now.

Next we will need to change the date column for `jh_recovered2` and `df` into dateformat in preparation for the merging process, repeat the same for both datasets.

In [9]:
jh_recovered2['date']=pd.to_datetime(jh_recovered2['date'], 
                                     errors='ignore')
df['date']=pd.to_datetime(df['date'], 
                          errors='ignore')

The date format has been rectified with the above code.

We noticed the country names are inconsistent between the 2 files for United States hence we will need to replace the names in the John Hopkins file `jh_recovered2` to match the Our World in Data `df`. The other country names are consistent.

In [10]:
jh_recovered2['Country/Region'] = jh_recovered2['Country/Region'].replace(['US'],'United States')

Before we can start merging, as the `jh_recovered2` data has its recovered cases split up based on the `Province/State` as opposed to the `df` data. Therefore, our first step is to ungroup the `jh_recovered2` `Province/State` to result in a sum of recovered cases for each country.

In [11]:
jh_recovered2_grouped=jh_recovered2.groupby(["Country/Region","date"]).sum()

Now the data has one daily value grouped by each country which is suitable for the merging process.

In order to join the datasets together, we need to find common variables to join them, ensuring the data matches up accordingly. Merge the two data sets based on the `location` & `date` variables in the 'Our World data'(`df`) and `Country/Region` & `date` variables in the John Hopkins data (`jh_recovered2`).

In [12]:
merge1=df.merge(jh_recovered2_grouped, 
                how='inner', 
                left_on=["location", "date"], 
                right_on=["Country/Region","date"])
merge1.head()

iso_code continent     location       date  total_cases  new_cases  \
0      AFG      Asia  Afghanistan 2020-01-22          NaN        0.0   
1      AFG      Asia  Afghanistan 2020-01-23          NaN        0.0   
2      AFG      Asia  Afghanistan 2020-01-24          NaN        0.0   
3      AFG      Asia  Afghanistan 2020-01-25          NaN        0.0   
4      AFG      Asia  Afghanistan 2020-01-26          NaN        0.0   

   new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  ...  \
0                 0.0           NaN         0.0                  0.0  ...   
1                 0.0           NaN         0.0                  0.0  ...   
2                 0.0           NaN         0.0                  0.0  ...   
3                 0.0           NaN         0.0                  0.0  ...   
4                 0.0           NaN         0.0                  0.0  ...   

   diabetes_prevalence  female_smokers  male_smokers  handwashing_facilities  \
0                 9.59             NaN           NaN                  37.746   
1                 9.59             NaN           NaN                  37.746   
2                 9.59             NaN           NaN                  37.746   
3                 9.59             NaN           NaN                  37.746   
4                 9.59             NaN           NaN                  37.746   

   hospital_beds_per_thousand  life_expectancy  human_development_index  \
0                         0.5            64.83                    0.498   
1                         0.5            64.83                    0.498   
2                         0.5            64.83                    0.498   
3                         0.5            64.83                    0.498   
4                         0.5            64.83                    0.498   

        Lat       Long  total_recovered  
0  33.93911  67.709953                0  
1  33.93911  67.709953                0  
2  33.93911  67.709953                0  
3  33.93911  67.709953                0  
4  33.93911  67.709953                0  

[5 rows x 53 columns]

From the above output, we can see the merge was successful, a new column for recovered cases `total_recovered` is added at the end of the dataframe.

The recovered column is a cumulative value of the cases recovered. Now we need to add a new column called `new_recover` that calculates the daily cases using the `total_recovered` variable, so that each value in `new_recover` corresponds to a daily value.

In [13]:
new_recover=[0]
rec=list(merge1["total_recovered"])
loc=list(merge1["location"])

for j in range(len(merge1)-1):
  if loc[j+1] == loc[j]:
    new_recover.append(rec[j+1]-rec[j])
  else:
    new_recover.append(0)

merge1["new_recover"]=new_recover
merge1.head()

iso_code continent     location       date  total_cases  new_cases  \
0      AFG      Asia  Afghanistan 2020-01-22          NaN        0.0   
1      AFG      Asia  Afghanistan 2020-01-23          NaN        0.0   
2      AFG      Asia  Afghanistan 2020-01-24          NaN        0.0   
3      AFG      Asia  Afghanistan 2020-01-25          NaN        0.0   
4      AFG      Asia  Afghanistan 2020-01-26          NaN        0.0   

   new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  ...  \
0                 0.0           NaN         0.0                  0.0  ...   
1                 0.0           NaN         0.0                  0.0  ...   
2                 0.0           NaN         0.0                  0.0  ...   
3                 0.0           NaN         0.0                  0.0  ...   
4                 0.0           NaN         0.0                  0.0  ...   

   female_smokers  male_smokers  handwashing_facilities  \
0             NaN           NaN                  37.746   
1             NaN           NaN                  37.746   
2             NaN           NaN                  37.746   
3             NaN           NaN                  37.746   
4             NaN           NaN                  37.746   

   hospital_beds_per_thousand  life_expectancy  human_development_index  \
0                         0.5            64.83                    0.498   
1                         0.5            64.83                    0.498   
2                         0.5            64.83                    0.498   
3                         0.5            64.83                    0.498   
4                         0.5            64.83                    0.498   

        Lat       Long  total_recovered  new_recover  
0  33.93911  67.709953                0            0  
1  33.93911  67.709953                0            0  
2  33.93911  67.709953                0            0  
3  33.93911  67.709953                0            0  
4  33.93911  67.709953                0            0  

[5 rows x 54 columns]

New column `new_recover` has been appended shown in the output above. A list is created and for each country we calculate the daily recovered cases starting with 0 for each country.


In the code below we will print out the minimum value for the new variable `new_recover`.

In [14]:
merge1['new_recover'].min()

-88158

As per the output above we can see that there exist some negative values. This can be explained due to negative corrections and adjustments in the recovered cases made by the original data sources.

Data munging has been completed. Now continue to subset the datasets.

Now we will subset the data so that it only includes the six countries that our data analysis is focused on - Australia, Brazil, India, Russia, South Africa and United States. To do this, first we will create a list containing the six countries this help improve the readability and assist in further analysis.

In [15]:
countries=['Australia', 'Brazil', 'India', 'Russia', 'South Africa', 'United States']

In [16]:
covid=merge1[merge1['location'].isin(countries)]

md("The subset consists of {} rows and {} columns now.".format(covid.shape[0],covid.shape[1]))

The subset consists of 1784 rows and 54 columns now.

The data is subsetted as the output above and renamed to `covid` for meaningful naming.

The other five datasets will also need to be subsetted so that we only include the six countries we are conducting analysis on. This will present a simpler view when the group conducts analysis. Below is a dictionary that stores the model names including the summary estimates, as keys and their respective data as values. The purpose is to reduce repition in code for future data cleaning. 

*The author of this section is: Cynthia Mather*

*The editor of this section is: Sherry Wang*

In [17]:
models_raw={"estimate":estimate_raw,"ICL":icl_raw,"IHME":ihme_raw,"LSHTM":lshtm_raw,"YYG":yyg_raw}

The data for the models can be subseted now to contain only the countries of interest, using a for loop to store the subsetted data in a new dictionary. 

In [18]:
models_clean={}
for key in models_raw.keys():
    models_clean["{}".format(key)]=models_raw.get(key)[models_raw.get(key)['Entity'].isin(countries)]

The above code has only kept the rows that belongs to the countries we are interested in.

Now we can continue to the data cleaning stage.

#### Data Cleaning

*The author of this section is: Sherry Wang*

*The editor of this section is: Cynthia Mather*

*start 8-11-2020 end 17-11-2020*

First, let's check if the the data types for each variables are appropriate.

In [19]:
covid.dtypes

iso_code                                      object
continent                                     object
location                                      object
date                                  datetime64[ns]
total_cases                                  float64
new_cases                                    float64
new_cases_smoothed                           float64
total_deaths                                 float64
new_deaths                                   float64
new_deaths_smoothed                          float64
total_cases_per_million                      float64
new_cases_per_million                        float64
new_cases_smoothed_per_million               float64
total_deaths_per_million                     float64
new_deaths_per_million                       float64
new_deaths_smoothed_per_million              float64
reproduction_rate                            float64
icu_patients                                 float64
icu_patients_per_million                     f

No changes in data types are required, since the data types are correct with numerical values in float64 type, date in datetime format and country codes and country names being objects.

Now we need to consider dealing with missing values by looking at the counts of the number of `NA` values in the datasets starting with `covid`.

In [20]:
covid.isna().sum(axis = 0)

iso_code                                 0
continent                                0
location                                 0
date                                     0
total_cases                             87
new_cases                               31
new_cases_smoothed                      34
total_deaths                           299
new_deaths                              31
new_deaths_smoothed                     34
total_cases_per_million                 87
new_cases_per_million                   31
new_cases_smoothed_per_million          34
total_deaths_per_million               299
new_deaths_per_million                  31
new_deaths_smoothed_per_million         34
reproduction_rate                      348
icu_patients                          1553
icu_patients_per_million              1553
hosp_patients                         1544
hosp_patients_per_million             1544
weekly_icu_admissions                 1748
weekly_icu_admissions_per_million     1748
weekly_hosp

From the output above, we can see that for many variables we have `NA` or missing values. These variables include `total_cases`, `new_cases`, `new_cases_smoothed`, `number of icu_patients`,`female_smokers`,`handwashing_facilities` naming a few. 

The appropriate method of dealing with missing values is to leave them in. For entries that have `NA`, we assume that this is because health officials in countries have not reported data for a specific attribute, this could be due to technology inabilities to collect certain information or other factors that impede the data collection. For example, during the early period of the pandemic, many countries began testing at different times and recording cases and therefore leading up to there first entry, data is considered as unreported. But when attributes have values, even 0, we assume heath officals for that country reported data. Therefore we will keep all missing values. 

Now let's continue to check if there exists any null value in the models datasets including `estimate`, `yyg`,`ihme`,`icl` and `ishtm`.

In [21]:
estimate=models_clean.get('estimate')
icl=models_clean.get('ICL')
ihme=models_clean.get('IHME')
lshtm=models_clean.get('LSHTM')
yyg=models_clean.get('YYG')

In [22]:
estimate.isna().sum(axis = 0)

Entity                                                                                             0
Code                                                                                               0
Date                                                                                               0
Daily new confirmed cases due to COVID-19 (rolling 7-day average, right-aligned)                  34
Daily new confirmed cases due to COVID-19 (rolling 7-day average, right-aligned) Annotations    1857
Daily new estimated infections of COVID-19 (ICL, mean)                                           242
Daily new estimated infections of COVID-19 (IHME, mean)                                          262
Daily new estimated infections of COVID-19 (YYG, mean)                                           474
Daily new estimated infections of COVID-19 (LSHTM, median)                                       935
dtype: int64

As printed above, we can see each infection case estimation model has a certain degree of incomplete data or null values. This is because the models each have a different update frequency approximately every 2 to 3 weeks, hence the data available to us is lagged in the dates. With some models ceased updates since August, this may be due to various reasons. Therefore, in this situation we should not replace the missing values with 0s, which could potentially decrease the accuracy or magnifying the uncertainties during the data cleaning stage. We will leave these values untouched so that they are not included in our later calculations of COVID-19's death rate.

Same process is required for the other 4 model estimation datasets. We will first check the data types of the variables in the datasets.

In [23]:
print(lshtm.dtypes)
print(estimate.dtypes)

Entity                                                                                           object
Code                                                                                             object
Date                                                                                             object
Daily new confirmed cases due to COVID-19 (rolling 7-day average, right-aligned)                float64
Daily new confirmed cases due to COVID-19 (rolling 7-day average, right-aligned) Annotations     object
Daily new estimated infections of COVID-19 (LSHTM, median)                                      float64
Daily new estimated infections of COVID-19 (LSHTM, lower)                                       float64
Daily new estimated infections of COVID-19 (LSHTM, upper)                                       float64
dtype: object
Entity                                                                                           object
Code                                              

*The author of this section is: Cynthia Mather*

*The editor of this section is: Sherry Wang*

Only 2 dataset types are printed here. Notice that the date variable needs to be changed into dateformat and this achieve through a for loop. 

In [24]:
for value in models_clean.values():
    value['Date']=pd.to_datetime(value['Date'], 
                                 errors='ignore')

All four estimation models plus the summary estimation datasets have been changed into dateformat.

Now for the ease of analysis and readability of the codes, we will replace the variable names that are untidy with short and meaningful variable names. The function below cleans the column names by inputing a model name and outputing a dictionary of the cleaned column names. The purpose of this function is to reduce duplicate code.

In [25]:
def clean_columns(model):
    scale="mean"
    if model=="LSHTM":
        scale="median"
    new_names={'Daily new confirmed cases due to COVID-19 (rolling 7-day average, right-aligned)':'daily new confirmed',
               'Daily new confirmed cases due to COVID-19 (rolling 7-day average, right-aligned) Annotations':'annotations',
               'Daily new estimated infections of COVID-19 ({}, {})'.format(model,scale):'{} {}'.format(model,scale),
               'Daily new estimated infections of COVID-19 ({}, lower)'.format(model):'{} lower'.format(model),
               'Daily new estimated infections of COVID-19 ({}, upper)'.format(model):'{} upper'.format(model)}
    return new_names

In the above code the long variable names for all four datasets have been replaced with a shorter name for later analysis.

The column names from the dataset of the four models can be cleaned using the for loop below. 

In [26]:
for key in models_clean.keys():
    if key!="estimate":
        models_clean.get(key).rename(columns=clean_columns(key),inplace=True)

Now the data cleaning (including cleaning null values and cleaning variable names) has been completed.


#### Outliers

*The author of this section is: Sherry Wang*

*The editor of this section is: Cynthia Mather*

*start 11-11-2020 end 17-11-2020*

Now moving on to checking existing outliers in the `covid` dataset. To visualise the outliers we will use box plots for the variables that will be used in later analysis and are not a constant value, this includes `total_cases`, `new_cases`, `new_cases_smoothed`, `total_deaths`, `new_deaths`, `new_deaths_smoothed` and `total_recovered and new_recover`.

In [27]:
variable_list=['total_cases','new_cases','new_cases_smoothed',
               'total_deaths','new_deaths','new_deaths_smoothed',
               'total_recovered','new_recover','total_tests','new_tests',
               'new_tests_smoothed']

box1 = make_subplots(rows=4, cols=2)
ntuple=([1,1],[1,2],[1,2],[2,1],[2,2],[2,2],[4,1],[4,2],[3,1],[3,2],[3,2])
for i,j in enumerate(range(len(ntuple))):
  box1.add_trace(
    go.Box(y=covid[variable_list[i]],name=variable_list[i],hoverinfo='skip'),
      row=ntuple[j][0], col=ntuple[j][1])
  
box1.update_layout(
          title={
              'text': "Distribution of COVID-19 Data",
              'y':0.96,
              'x':0.5,
              'xanchor': 'center',
              'yanchor': 'top'})
box1.show()

From the box plot outputted above, we can observe that all the variables are rightly skewed for `new_deaths`,`new_tests` and `new_cases` and also indicates there are some outliers on the larger end. However, these outliers does not exist as we look at the corresponding smoothed variable (`new_deaths_smoothed`,`new_tests_smoothed` and `new_cases_smoothed`), these variables smoothed over 7 days removes the outliers. As these outliers reconciles data from previous days and is not incorrect, we can keep this entry in the dataset. Number of cases on a given day does not necessarily represent the actual number on that date since it has a long reporting chain, both large and negative values can be made to a country's entire time series to correct values retrospectively.This is just an example of how time variation and delays occur when studying an ongoing pandemic with information provided by [Our World in Data Source](https://github.com/owid/covid-19-data/tree/master/public/data). In the following analysis we will be focusing on using variables that are smoothed to remove the uncertainties by the reconciliations made from the data sources. 

Now that the data has been cleaned and formated, we can move on to undersanding the data essential for the analysis.

### B.2. Exploratory Data Analysis for Selected Countries

*The author of this section is: Johnson Yun*

*The editor of this section is: Cynthia Mather & Sherry Wang*

*start 8-11-2020 end 18-11-2020*

In this section, exploratory data analysis is conducted to investigate how the pandemic has panned over time across the six countries of interest. The main characteristics explored will be the visuaisations and correlations between factors that assist in the formulation of the driving question. 

The code below creates a dictionary to store the discrete colour names in plotly for each selected country. The main reason behind using Plotly for the graphs in this entire notebook is due to its *interactive features*. The features are useful for reading exact results, simplifying visualisations and most importantly, considers the colour sensitivity of potential viewers. Some people like to visualise information and some like to read and the acknowledgement of these different mental models is achieved by including the interactive features in each graph. The purpose of this is to follow the *principle of consistency* such that each country is distinctively represented by a colour. The colours chosen vary between each other to account for colour sensitivity in viewers and are bold such that they contrast with the white background to assist for text readability. Finally these different colours considers *Miller's Law* of choosing $5±2$ colours (six colours) to account for the short-term memory of individuals. 

In [28]:
dict_colours={"Australia":"gold","Brazil":"forestgreen","India":"tomato",
              "Russia":"crimson","South Africa":"mediumpurple","United States":"dodgerblue"}

The code below shows a preview of the main dataset, `covid`. 

In [29]:
covid.head()

iso_code continent   location       date  total_cases  new_cases  \
2146      AUS   Oceania  Australia 2020-01-22          NaN        0.0   
2147      AUS   Oceania  Australia 2020-01-23          NaN        0.0   
2148      AUS   Oceania  Australia 2020-01-24          NaN        0.0   
2149      AUS   Oceania  Australia 2020-01-25          1.0        1.0   
2150      AUS   Oceania  Australia 2020-01-26          4.0        3.0   

      new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  ...  \
2146               0.000           NaN         0.0                  0.0  ...   
2147               0.000           NaN         0.0                  0.0  ...   
2148               0.000           NaN         0.0                  0.0  ...   
2149               0.143           NaN         0.0                  0.0  ...   
2150               0.571           NaN         0.0                  0.0  ...   

      female_smokers  male_smokers  handwashing_facilities  \
2146            13.0          16.5                     NaN   
2147            13.0          16.5                     NaN   
2148            13.0          16.5                     NaN   
2149            13.0          16.5                     NaN   
2150            13.0          16.5                     NaN   

      hospital_beds_per_thousand  life_expectancy  human_development_index  \
2146                        3.84            83.44                    0.939   
2147                        3.84            83.44                    0.939   
2148                        3.84            83.44                    0.939   
2149                        3.84            83.44                    0.939   
2150                        3.84            83.44                    0.939   

           Lat       Long  total_recovered  new_recover  
2146 -256.8502  1130.8439                0            0  
2147 -256.8502  1130.8439                0            0  
2148 -256.8502  1130.8439                0            0  
2149 -256.8502  1130.8439                0            0  
2150 -256.8502  1130.8439                0            0  

[5 rows x 54 columns]

The code below creates a function that takes in two strings, an attribute from the `covid` dataset such as `total deaths` and a title. The function using plotly, plots different attributes for all six countries to gain an understanding and compare the trends.

In [30]:
def eda(variable,title):
    fig = px.line(covid, x="date", y=variable, 
                  color="location", color_discrete_sequence =list(dict_colours.values()),
                 hover_data={"location":False,"date":False,variable:':.0f'})
    fig.update_layout(plot_bgcolor="white")
    fig.update_xaxes(title_text="Date",tickangle = 290)
    fig.update_yaxes(title_text="Cases")
    fig.update_layout(hovermode="x unified")
    fig.update_layout(
        title={'text': title,
              'y':0.95,'x':0.5,
              'xanchor': 'center','yanchor': 'top'})
    fig.update_layout(
        legend=dict(
            x=0.05,y=0.95,
            bordercolor="Black",
            borderwidth=2))

    fig.show()

The code calls the `eda` function and plots new cases smoothed. The `new_cases_smoothed` variable contains the number of new cases each day smoothed over 7 days to visualise data that is not noisy. Noisy data that comes from new case entries each day such as health officials accounting for past cases can cause features in the trends that are misunderstood.

In [31]:
eda("new_cases_smoothed","New cases (smoothed) around the world")

*The author of this section is: Cynthia Mather*

*The editor of this section is: Sherry Wang*

*start 10-11-2020 end 18-11-2020*


From the output above, we can visualise that the United States is currently increasing in the number of new cases each day with no signs of a plateu any time soon. One of the biggest causes for this trend is due to the current state of the country with protests that has increased the number of people on the streets rather than social distancing, resulting in higher cases. India, Brail and South Africa show a reduced number of daily confirmed cases, yet Russia begins to increase. The daily smoothed cases for Australia appear to be very small comparatively. While this form of visualisation is easy to understand by the general public, a fairer comparison between cases in different countries is using a logarithmic plot. Logarithmic plots are ideal for measuring rates of changes and particularly rates of growth.


To account for viewers who are colour sensitive or colour blind, all plots have their interactivity on by plotly so if colours can not be viewed at its best potential, viewers can read results and still see trends between different variables. However in an attempt to account for this and therefore make improvements, all plots created were loaded into a colour blind simulator that can be found here: https://www.color-blindness.com/coblis-color-blindness-simulator/ . This simular was used to upload a plot can alter the colour sensitivity of the graph to understand how it looks like to someone who is colour sensitive or colour blind. Each plot will be viewed differently i.e. anomalous trichromacy, dichromatic view and monochromatic view to account for different levels of colour blindness. 

For this graph, we simulated Red-Weak/Protanomaly which is a form of colour deficiency in the red componants and therfore users only see blue components. 

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/red-weak.JPG?token=AAABCWLAXOYIKFNHWKXFRT27XXAFC)

All colours are still distinguishable.


The code below is a function similar to `eda` except it plots the log of the y axis. The purpose is to better see trends especially for countries with comparitivily lower results like Australia and also assist us to better determine the rates of growth.

In [32]:
def eda_log(variable,title):
    fig = px.line(covid, x="date", y=variable, 
                      color="location", hover_name="location",
                      color_discrete_sequence =list(dict_colours.values()),
                      hover_data={'location':False,'date':False, variable:':.1f'},log_y=True)
    fig.update_layout(plot_bgcolor="white")
    fig.update_xaxes(title_text="Date",tickangle = 290)
    fig.update_yaxes(title_text="log(Cases)")
    fig.update_layout(
          title={'text': title,
              'y':0.96,'x':0.5,
              'xanchor': 'center','yanchor': 'top'})
    fig.update_layout(
        legend=dict(
            x=0.005, y=0.95,
            bordercolor="Black",
            borderwidth=2)) 
    fig.update_yaxes(nticks=10)
    fig.show()

The code below plots the new cases smoothed on a log scale by calling the function, `eda_log`. 

In [33]:
eda_log("new_cases_smoothed","COVID-19 Log new cases (smoothed) around the world")

We can clearly see with the logarithmic plot above Australia's trends for daily new cases can be observed. From the graph above it is also clear that the recorded cases was not complete or some countries did not have confirmed cases in February. Also comparing Australia's daily new cases it shows a much slower rates of increase than the other countries.

Next using the same `eda_log` function we will plot below for `total_deaths`.

In [34]:
eda_log("total_deaths","COVID-19 Log total deaths around the world")

Again, from this logarithmic graph we can identify countries with higher rates of increase in the numbers of total deaths. United States with a much higher rate in comparison to Australia.

For this graph, we simulated Green-Weak/Protanomaly which is a form of colour deficiency in the green components and therefore users see greens more pale.

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/green-weak.JPG?token=AAABCWJ5V6TBUTVRCJICVO27XW7VE)

All colours are still distinguishable.

The same function is called on the variable `total_recovered`.

In [35]:
eda_log("total_recovered","COVID-19 Log total recoveries around the world")

From the output above, the rates of growth for total recovered cases across different countries can be compared.
Next the same steps are conducted for `new_tests_smoothed`.

In [36]:
eda_log("new_tests_smoothed","COVID-19 new tests (smoothed) around the world")

For the new daily tests `new_tests_smoothed`, we can find that the graph looks a bit strange. That's because after taking the log of the data, some countries which do not record a daily test at some dates will go straight down, so we can find that, in Brazil, they do not have a test each day potentially due to insufficient medical resources. Furthermore, we can also notice that each country has a different start day of recording the number of tests taken. 

For this graph, we simulated Blue-Weak/Protanomaly which is a form of colour deficiency in the blue components and therfore users see blue very pale. 

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/blue-weak.JPG?token=AAABCWIDB562WJF5MZPF2PS7XW7Q2)

All colours are still distinguishable.

*The author of this section is: Johnson Yun*

*The editor of this section is: Sherry Wang*

*start 13-11-2020 end 18-11-2020*


Lastly, we will investigate in the correlations between multiple variables by displaying the correlation matrix between multiple variables in all selected countries.

In [37]:
columns = ['total_cases', 'new_cases', 'total_deaths', 'new_deaths', 'total_tests', 'new_tests']
corr = merge1[columns].corr()
corr.style.background_gradient(cmap='coolwarm').set_precision(2)

From the correlation matrix above, it is easy to spot the variables that are independent from each other and the variances that have strong correlations. The matrix used a red and blue scale, where the more satuarated the red shade the stronger the positive relationship exists. On the other hand, ones with blue shades have weaker correlations and goes to the negative side of the scale.

According to the correlation matrix above we can identify that total_cases has a strong relationship with `total_deaths`, it also has a strong positive correlation with `total_tests`.

### B.2. Individual Country Analysis

*The author of this section is: Cynthia Mather*

*The editor of this section is: Sherry Wang*

*start 7-11-2020 end 18-11-2020*

All plots in plotly and all values (IFR) to appropriate number of significant figures (i.e. one significant figure for uncertainty) 


In many media and articles that is released to the public, there exists many numbers that are stated as the death rate of COVID. However, these death rates can be very misleading for the stakeholders. As there are many confusions and uncertainties in the methods of calculation, the timeframe captured by the death rate, and ways of visualising the death rates.

The most commonly used calculation that is published to the public is the Case Fatality Rate (CFR) which is the number of deaths from the disease divided by the number of diagnosed cases of the disease. However, CFR actually does not reflect the risk of death because when situations were there are people who have COVID but are not diagosed, the CFR will overestimate the true risk of death. Also in another situation when some people are currently sick and will die of the disease, but have not died yet, the CFR will underestimate the true risk of death.
Therefore, as the limitation stated above, in this notebook we will be addressing the Infection Fatality Rate (IFR) which is a method researchers use that can most accurately reflect the mortality of a disease. It is the number of infected people who die as a result (including those who don't get tested or show symptoms) divided by the number of infected people (including both the confirmed and unconfirmed cases).
However, note that there exists problems with calculating such rate is that most of the data is unavailable (i.e. those infected but not confirmed through testing), there are different severities with mild or no symptoms whos infection goes undetected and the time difference between infection and death is quite long. Because of these challenges, many information reported to the public is the Case Fatality Rate (CFR) as it utilises available data and is more easily understood by the public. 




#### Case Fatality Rate (CFR)

We will first explore the CFR as a percentage using the equation:

$CFR=\frac{number\ of\ deaths\ from\ COVID-19}{number\ of\ confirmed\ cases\ from\ COVID-19}*100$ 


The code below calculates CFR as a function of time using the formula stated above. This is stored as another variable called `total_CFR` in the `covid` dataset.

In [38]:
covid['total_CFR']=(covid["total_deaths"]/covid["total_cases"])*100

The function below plots the CFR as a function of time for the country passed through the function (all six countries). The purpose is to look at the trends for individual countries over time without code duplicates. 

In [39]:
fig=px.line(covid,x="date",y="total_CFR",
            color="location",color_discrete_sequence =list(dict_colours.values()))
fig.update_xaxes(title_text="Date",tickangle = 290)
fig.update_yaxes(title_text="CFR (%)")
fig.update_layout(
    title={'text': "Case Fatality Rate around the world",
        'y':0.95,'x':0.5,
        'xanchor': 'center','yanchor': 'top'})
fig.update_layout(plot_bgcolor="white")
fig.update_layout(
        legend=dict(
            x=0.8, y=0.95,
            bordercolor="Black",
            borderwidth=2)) 
fig.show()

During the begining of the pandemic, the spread of the CFR for the six countries is quite large such that in May, the difference of the highest (Brazil) and lowest (Russia) CFR is about 6%. However,from August onwards, the CFR begins to converge and begins to plateu in October with a differnce of about 2.7%. It is evident that the CFR is inconsistent over time and varies between different countries. As there are people who have the disease but aren't diagnosed, this CFR overestimates the true risk of death and this over and underestimation occurs due to the time period between confirmed cases and deaths or recoveries as mentioned previously.


#### Infection Fatality Rate

The purpose of this section is to present and compare the **Infection Fatality Rate(IFR)** among the six countries as a pecentage, using the equation: 
$IFR=\frac{number\ of\ deaths\ from\ COVID}{number\ of\ infected\ individuals\ from\ COVID}*100$

The next step is deciding which model is most appropriate in estimating the daily infections. The different models obtained from https://ourworldindata.org/covid-models outlines what the model is based on and the key assumptions and potential limitations for each.
A couple of features of the models include: 

Imperial College London (ICL): 
* Age-structured susceptible-exposed-infectious-recovered (SEIR) model focuses on low and middle-income countries
* Model uses age and country-specific data on demographics patterns of social contact, hospital availability and risk of hospitalisation and death
* assumes sufficient access to healthcare
* assumes change in transmission over time is a function of average mobility trends


The Institute for Health Metrics and Evaluation (IHME)
* Model uses different data to simulate transmission and disease progression: mobility, social distancing policies, population density, pneumonia seasonality and death rate, air pollution, altitude, smoking rates and self-reported contacts and mask use. 
* death model assumes relationship between confirmed deaths, confirmed cases and testing levels. For example, decreasing CFR is reflective of increasing testing and shift toward testing mild or asymptomatic cases.


Youyang Gu (YYG)
* Model created and optimised for the US
* Assumptions on how reopening will affect social distancing and ultimately transmission. 


The London School of Hydiene & Tropicala Medicine (LSHTM)
* Assumes delay adjusted CFR of 1.4% baseline that does not account for different age distributions outside China. This means there is an overestimation for younger populations and underestimation in countries with older populations.

A full description can be found in the link above. 

To choose the most appropriate model, we require the model with lowest uncertainties as this generally reflects extensive data availability, large studies and data that are consistent across sources (which Cynthia found in the "Uncertainty between different datasets" section in her Australia analysis: https://github.sydney.edu.au/swan9801/R13B-Group4-COVID/blob/master/Process%20Notebooks/Checkpoint%201/Checkpoint%201-%20Cynthia.ipynb ). 


We can look at an India as an example to see which model has the smallest 95% confidence interval. 

The code below subsets the ihme model data for india.

In [40]:
ihme_india=ihme[ihme["Entity"]=="India"]

The code below plots the number of infected indivduals (confirmed and unconfirmed) to the confirmed reports. 

In [41]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=ihme_india["Date"], 
                         y=ihme_india["IHME mean"],
                         line=dict(color='DarkViolet', width=4), name="IHME model with "))

fig.add_trace(go.Scatter(x=ihme_india["Date"], 
                         y=ihme_india["IHME lower"],
                         line=dict(color='mediumPurple', width=4,dash='dot'), showlegend=False))

fig.add_trace(go.Scatter(x=ihme_india["Date"], 
                         y=ihme_india["IHME upper"],
                         line=dict(color='mediumPurple', width=4,dash='dot'),
                         fillcolor="rgba(0,40,100,0.2)", fill = 'tonexty',showlegend=False))
fig.add_trace(go.Scatter(x=ihme_india["Date"], 
                         y=ihme_india["daily new confirmed"],
                         line=dict(color='fuchsia', width=4), name="Confirmed"))



fig.update_xaxes(title_text="Date",tickangle = 290)
fig.update_yaxes(title_text="Number of Estimated Infections")
fig.update_layout(
    title={
        'text': "Average daily estimated infections using IHME model with 95% CI",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'})
fig.show()

This model outputs a very small confidence interval for India. Further, as this model contains a small confidence interval for all other countries, we will use this model. Refer to individual process notebooks in checkpoint 2 for more model selection analysis. Link to checkpoint 2 folder in GitHub: https://github.sydney.edu.au/swan9801/R13B-Group4-COVID/tree/master/Process%20Notebooks/Checkpoint%202

The code below stores the name of the model being used.

In [42]:
model_data = ihme

The code below will plot the estimate number of infections  for all six countries and compares this to the confirmed number of cases reported. 

In [43]:
c_list=['Australia','Brazil','India','Russia','South Africa','United States']

ntuple=([1,1],[1,2],[2,1],[2,2],[3,1],[3,2])


fig1 = make_subplots(rows=3, cols=2, subplot_titles=('Australia','Brazil','India','Russia','South Africa','United States'))
for i,j in enumerate(range(len(c_list))):
    
    model_country = model_data[model_data["Entity"]==c_list[i]]
    country_colour = dict_colours[c_list[i]]
    fig1.update_layout(legend=dict(
            orientation="h",
            yanchor="bottom",
            y=1.05,
            xanchor="right",
            x=1.05
        ))


    fig1.add_trace(go.Scatter(x=model_country["Date"], 
                             y=model_country["IHME mean"],
                             line=dict(color=country_colour, width=3),showlegend=False,  name="Estimation"),row=ntuple[j][0], col=ntuple[j][1])

    fig1.add_trace(go.Scatter(x=model_country["Date"], 
                             y=model_country["IHME lower"],
                             line=dict(color='grey', width=0.5),  name="Lower Bound", showlegend=False),row=ntuple[j][0], col=ntuple[j][1])

    fig1.add_trace(go.Scatter(x=model_country["Date"], 
                             y=model_country["IHME upper"],
                             line=dict(color='grey', width=0.5),
                             fillcolor="rgba(0,40,100,0.2)", fill = 'tonexty',name="Upper Bound",showlegend=False),row=ntuple[j][0], col=ntuple[j][1])
    
    fig1.add_trace(go.Scatter(x=model_country["Date"], 
                             y=model_country["daily new confirmed"],
                             line=dict(color=country_colour, width=3,dash = "dot"),showlegend=False, name="Confirmed"),row=ntuple[j][0], col=ntuple[j][1])
   
    
fig1.update_layout(height=600, width=1000)
    
fig1.update_xaxes(title_text="Date")
fig1.update_yaxes(title_text="Number of Cases")

fig1.update_layout(
            title={'text': "Average daily infections using IHME model for Countries with 95% CI",
                'y':0.95,'x':0.5,
                'xanchor': 'center','yanchor': 'top'})

fig1.add_annotation(text="The --- (dotted) lines are the confirmed infections and the - (solid) lines are the estimated infections with 95% confidence interval in grey",
                      xref="paper", yref="paper",
                      x=0.5, y=1.1,showarrow=False)
fig1.update_layout(plot_bgcolor="white")




The estimated infections for all countries is much higher than the confirmed infections. The large difference are seen more distinctively in the peaks. 

For this graph, we simulated Red-Blind/Protanopia which is a form of colour deficiency where indivduals see no difference between red, orange, yellow and green.

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/red-blind.JPG?token=AAABCWIKQCZ2EMCO7NWC3AK7XW5HK)

While some colours are indistinguishable like South Africa and the United States, the choice of putting theses plots as separate subplots distinctively with titles effectively separates the countries to account for this form of colour blindness. The interactivity is also critcal in helping to distinguish the colours further. 







The code below creates a function that calculates the IFR using one input, the name of the country. Embeded in the function, `calculate_IFR` is another function called `round_to_1` that ensures that that the uncertainity is written to 1 significant figure. In science, when writing a `value ± uncertainity`, the `uncertainity` must be written to 1 significant figure and the `value` to the same number of decimal places as the `uncertainity`.The function below accounts for this format and returns the the IFR and its uncertainty for a given country.

In [44]:
def calculate_IFR(country):
    covid_country=covid[covid["location"]==country]
    model_country=model_data[model_data["Entity"]==country]

    ifr_model=covid_country["total_deaths"].max()*100/model_country["IHME mean"].sum()
    ifr_model_upper=covid_country["total_deaths"].max()/model_country["IHME upper"].sum()
    ifr_model_lower=covid_country["total_deaths"].max()/model_country["IHME lower"].sum()
    error_range=abs(ifr_model_upper-ifr_model_lower)*100/2
    
    def round_to_1(x):
        return round(x, -int(floor(log10(abs(x)))))
    
    u=round_to_1(error_range)
    dp=str(u)[::-1].find('.')
    
    return [round(ifr_model,dp),u]

We can calculate the IFR with uncertainities for all countries of interest using in the IHME model.

The code below creates an empty data frame with 3 column headings, `location`,`IFR` and `Uncertainty`. The purpose of this code is make available a data storage place in which the all data can be accessed from the one dataset.

In [45]:
IFR_relation=pd.DataFrame(columns=["location", "IFR", "Uncertainty"])

The code below calculates the IFR and uncertainty for a country using the `calculate_IFR` function above. By looping over each country, the country name and its calculated IFR and uncertainity are appended to the `IFR_relation` dataframe. The purpose of this is create a complete dataframe that has the respective death rates with uncertainties for each country of interest.

In [46]:
for i in range(6):
    IFR,U=calculate_IFR(countries[i])
    IFR_relation.loc[i]=[countries[i],IFR,U]

The code below prints the new dataframe, `IFR_relation`. The purpose of this is to give the reader an understanding of what this dataset looks like that look at how the rate varies for each country.

In [47]:
fig = go.Figure(data=[go.Table(
    header=dict(values=list(IFR_relation.columns),
                fill_color='salmon',
               line_color='darkslategray'),
    cells=dict(values=[IFR_relation.location, IFR_relation.IFR, IFR_relation.Uncertainty],
               fill_color='white',
               line_color='darkslategray'))
])

fig.update_layout(title_text="Table 1: COVID-19 Death (Infection Fatality) Rate with 95% Confidence Intervals",
)

fig.show()

From the table above, we can clearly comprehend the Infection Fatality Rate and its associated uncertainties. What stands out is that Australia has the highest death rate and uncertainity. While the dataset is small, it is difficult to see if there are any trends and therefore these results needs to be futher analysed and visualised in the next section. 

### B.3. Uncertainty Visualisations

*The author of this section is: Cynthia Mather*

*The editor of this section is: Cynthia Mather & Sherry Wang*

*start 7-11-2020 end 18-11-2020*

This final section aims to answer the second half of the driving question of visualising the uncertanties in a meaningful way. By visualising these uncertainities from the IFR (death rate) in a meaningful way, we can explore potential confounding factors and present them in a way that is understood by our stakeholders. In the end, we will present three main graphs that visualise the deadliness of COVID-19 in each country and the uncertainities in a clean and understandable way.

#### B.3.1. Linear Regression

To do so, we need to first create a dataset that contains the attributes for each country. 

The code below lists the attributes of a country.

In [48]:
country_attribute=["location","iso_code",'population', 'population_density', 'median_age', 'aged_65_older',
       'aged_70_older', 'gdp_per_capita', 'extreme_poverty',
       'cardiovasc_death_rate', 'diabetes_prevalence', 'female_smokers',
       'male_smokers', 'hospital_beds_per_thousand',
       'life_expectancy', 'human_development_index']

Since all attributes are constant over our period, we remove the duplicated entries.

In [49]:
d_unique=covid[country_attribute].drop_duplicates()

To aid in the visualisation process, we merge the IFR and uncertainity dataset with the respective country attributes and return the new merged dataset for viewers to see the new dataset for analysis. 

In [50]:
IFR_attribute=pd.merge(IFR_relation,d_unique,on="location")
IFR_attribute

location   IFR  Uncertainty iso_code    population  \
0      Australia  1.10         0.30      AUS  2.549988e+07   
1         Brazil  0.36         0.03      BRA  2.125594e+08   
2          India  0.20         0.01      IND  1.380004e+09   
3         Russia  0.58         0.05      RUS  1.459345e+08   
4   South Africa  0.29         0.07      ZAF  5.930869e+07   
5  United States  0.77         0.06      USA  3.310026e+08   

   population_density  median_age  aged_65_older  aged_70_older  \
0               3.202        37.9         15.504         10.129   
1              25.040        33.5          8.552          5.060   
2             450.419        28.2          5.989          3.414   
3               8.823        39.6         14.178          9.393   
4              46.754        27.3          5.344          3.053   
5              35.608        38.3         15.413          9.732   

   gdp_per_capita  extreme_poverty  cardiovasc_death_rate  \
0       44648.710              0.5                107.791   
1       14103.452              3.4                177.961   
2        6426.674             21.2                282.280   
3       24765.954              0.1                431.297   
4       12294.876             18.9                200.380   
5       54225.446              1.2                151.089   

   diabetes_prevalence  female_smokers  male_smokers  \
0                 5.07            13.0          16.5   
1                 8.11            10.1          17.9   
2                10.39             1.9          20.6   
3                 6.18            23.4          58.3   
4                 5.52             8.1          33.2   
5                10.79            19.1          24.6   

   hospital_beds_per_thousand  life_expectancy  human_development_index  
0                        3.84            83.44                    0.939  
1                        2.20            75.88                    0.759  
2                        0.53            69.66                    0.640  
3                        8.05            72.58                    0.816  
4                        2.32            64.13                    0.699  
5                        2.77            78.86                    0.924

As the `IFR_attribute` dataset is small, by inspection there are no missing values and therefore the dataset can be used for analysis. To understand which attributes are potential confounding factors, we can simulate simple linear regression models, then understand in depth the attributes with high correlation coefficients. To perform this, the attributes will be the x variable and the IFR will be the y. The reason for simulating simple linear regresssion models independently is that the variables are not independent such as the aged proportions, which is an assumption required to be satisfied.

To begin, the cold below creates a new dataframe in which we aim to store the simulated simple linear regression models in the one dataset for visualisation purposes.

In [51]:
correlation=pd.DataFrame()

As we are interested in the attributes of the countries, we need to remove the location variables i.e. `location` and `iso_code` and append these values in the currently empty dataset, `correlation`. 

In [52]:
country_attribute.remove("location")
country_attribute.remove("iso_code")
correlation["attribute"]=country_attribute

The code below is a for loop that loops over each attribute of a country and fits a linear regression model with the IFR for all the countries. The purpose of this is to understand which variables are best correlated with the IFRs for all countries and therefore by fitting a linear regression model from the `sklearn` package, there coefficient of determination or $R^2$ is stored in the empty vector above. 

In [53]:
model_coef=[]
for attribute in country_attribute:
    X = np.array(IFR_attribute[attribute]).reshape((-1, 1))
    y = np.array(IFR_attribute['IFR'])

    model = LinearRegression()
    model.fit(X, y)

    model_coef.append(float((model.score(X,y))))
correlation["coef"]=model_coef

We can visualise these scores to illustrate attributes with high correlation to the IFR and therefore potential confounding factors. The code below plots the scores of the models as bar plots for each attribute such that attributes with high correlations, above 0.7, indicated by a black horizontal line are in green and the rest in red. The choice of colours accounts for colour sensitive in some viewers by using warmer tones and avoiding blues. 

In [54]:
# create criteria for correlation using threshold
threshold=0.75
colors = ['High Correlation' if c > threshold else 'Low Correlation' for c in model_coef]

# plot bar plot
fig = px.bar(correlation,
    x="attribute", y="coef",
    labels=dict(attribute='Feature', coef='Coefficient of Determination'),
             color=colors,
             color_discrete_sequence=['red', 'green']
)

# add horizontal line to visualise threshold
fig.add_shape(type='line',
                x0=0,
                y0=threshold,
                x1=13.5,
                y1=threshold,
                line=dict(color='Black'),
                xref='x',
                yref='y'
)

# visualise x axis ticks at an angle 
fig.update_xaxes(tickangle = 290)

# add title
fig.update_layout(
        title={
            'text': "Linear Regression model of Infection Fatality Rate",
            'y':0.95,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top'})

# add legend
fig.update_layout(legend=dict(
    orientation="h",
    yanchor="bottom",
    y=0.9,
    xanchor="right",
    x=1.0,title=""))

# create white background
fig.update_layout(plot_bgcolor="white")

# show plot
fig.show()

The best correlated attributes with the IFR are: `human_development_index`, `gdp_per_capita` and `aged_65_older`. These attributes tells us there is a strong linear correlation between these variables and the IFR, suggesting that they are confounding factors that infleunce the death rates of COVID in each country. Hence, we need to address them in our visualisations to interpret the uncertainty factors.

Note the choice of colours, red and green as we considered viewers were colour sensitive which is more frequent in the blue frequency range. 

For this graph, we simulated Green-Blind/Protanomaly which is a form of colour deficiency in the blue components and therfore users see blue very pale. 

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/green-blind.JPG?token=AAABCWMIUZNU55NM4CESP7K7XW5KK)

These two colours are very similar and can not be distinugished easily. However to account for this, the added horizontal line shows the threshold such that any attributes with scores above this line are of high correlation and any attributes below have low correlations. 


#### B.3.2. Uncertainty visualisations

As the data from `aged_65_older` and `aged_75_older` are dependent for a given country, we will only consider the `aged_65_older` as we assume they have similar results. Therefore we will further explore the attributes: `human_development_index`, `aged_65_older` and `gdp_per_capita`.  

##### Visualisation 1: Barplot

The code below looks at two variables: `aged_65_older` and `human_development_index`. `aged_65_older` contains the share of the population that is 65 years and older in the most recent year. As our time frame is one year, this variable does not change accross time and therefore is constant for each country. `human_development_index` is considered a summary score that measures achievement in key dimensions of human development. These dimensions include: a long healthy life, being knowledgable and having a decent standard of living. Similarly, for our one year period, this score is constant over time in the dataset but varies between different countries. 


In [55]:
def plot_uncert(attribute,title):
    
    # plot bar plot
    fig=px.bar(IFR_attribute,
           x="location",
           y="IFR", 
           color=attribute,
           error_y="Uncertainty",
          labels=dict(location="Country", IFR="IFR (%)", attribute=title),hover_name="location",
              hover_data={"location":False,
                         attribute:':.2f'})
    
    #  arrange bars to be ascending (Gesalt principle)
    fig.update_xaxes(categoryorder='total ascending')
    
    # add subtitle
    fig.add_annotation(text="Hover over each bar to observe the correlation between the {} and Infection Fatality Rates (IFR) ".format(title),
                      xref="paper", yref="paper",
                      x=0.6, y=1.06,showarrow=False)
    
    # add title
    fig.update_layout(
        title={
            'text': "COVID-19 Death (Infection Fatality) Rate with 95% Confidence Intervals",
            'y':0.95,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top'})
    
    #create white background 
    fig.update_layout(plot_bgcolor="white")
    
    #show plot
    fig.show()

Firstly, we can compare the different Infection Fatality Rates as percentages for different countries. We can visulise this using bar plots in plotly and combine a third variable, the `human_development_index` for each country  as a colour gradient. The purpose of this comparision is to identify any trends between a potential confounding variable and the death rate in a country due to COVID-19. The code below plots the countries on the x axis and IFR on the y axis with uncertainty levels indicated by the error bars.

In [56]:
plot_uncert("human_development_index","Human Development Index (HDI)")

 There is a correlation between human development index and IFR in the plot above. As the IFRs are visualised in ascending order, the colour scheme follows indicating that this variable is a plausible confounding factor to the deathy rates in each country. For countries with low human development indexes, the death rate is low but for countries with high human development indexes, the death rate is higher.

 
The colour scheme choice accounts for viewers who are colour sensitive by choosing warmer tones over blues. Furthermore, the sorting of the bars assists viewers to form a correlation with HDI by considering the human perception and Gestalt principle. 

For this graph, we simulated Blue-blind/Protanomaly which is a form of colour deficiency in the blue components and therfore users see blue very pale. 

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/blue-blind.JPG?token=AAABCWOEQHM7E2HMSGSJMUK7XW5NO)

All colours are still distinguishable.

We can plot a similar graph as above, comapring IFR in different countries but see if there is a trend between the population proportion aged 65 years and older `aged_65_older`. The code below plots the countries in the x axis, IFR in the y axis with error bars and the colour is associated with the aged proportions for each country for the most recent year avaliable.

In [57]:
plot_uncert("aged_65_older","Proportion Aged >65")

There is a trend for the the population aged 65 years and older and the IFR of COVID-19 in the countries of interest. For countries with a higher proportion of elderly people sich as the United States and Australia, the IFR is significantly higher. Similarly, for countries with a lower proportion of elderly population such as India and South Africa, the infection fatality rate is lower, under the 0.4% mark. The figure above shows a corrlection between these two variables but there is an inconsistency with the IFR with South Africa. If we assume this relation between age and IFR, the IFR for South Africa should be lower than India, given by its smaller proportion of individuals aged 65 years and older. However, as the error bars for South Africa and India overlap in range, we can assume this inconcistancy is caused by the uncertainity in IFR calculations. Therefore we conclude that there is a correlation between age and IFR such that for countries with higher proportion of individuals aged 65 years and older, the Infection Fatality Rate is higher.



##### Visualisation Two: Scatter plot

As confidence intervals and error bars are commonly used in science, audiences such as the general public may have difficulties in interpreting uncertainties presented in this manner. We have considered another method of visualising these uncertainties in the IFR by a scatter graph. 

The code below calculates the minimum and maximum IFR based on the 95% confidence interval and appends it to the dataset, `IFR_attribute`. The purpose is to assist in the visualisation of these errors. 

In [58]:
IFR_attribute["Minimum IFR"]=IFR_attribute["IFR"]-IFR_attribute["Uncertainty"]
IFR_attribute["Maximum IFR"]=IFR_attribute["IFR"]+IFR_attribute["Uncertainty"]

The code below plots a scatter plot with `gdp_per_capita` on the x axis, `human_development_index` on the y axis, the colour of the markers representing each country and its size representing the IFR. The key feature is the rings of the marker that indicate the lower and upper bounds of the uncertainties. 

In [59]:
# plots the maximum IFR
fig=px.scatter(IFR_attribute,x="gdp_per_capita",
               y="human_development_index",
               size="Maximum IFR", 
               color='location',opacity=1,
              labels=dict(gdp_per_capita="GDP per Capita", human_development_index="Human Development Index", 
                          location="Country"),size_max=30,
              color_discrete_sequence =list(dict_colours.values()),custom_data=["location","Minimum IFR","Maximum IFR"])

# update hover info
fig.update_traces(
    hovertemplate="<br>".join([
        "<b>%{customdata[0]}</b><br>",
        "GDP per Capita: %{x:$,.0f}",
        "HDI: %{y:.2f}",
        "Minimum IFR: %{customdata[1]:.2f}",
        "Maximum IFR: %{customdata[2]:.2f}",
    ])
)

#add minimum IFR
fig.add_scatter(x=IFR_attribute["gdp_per_capita"], y=IFR_attribute["human_development_index"], mode="markers",
                marker=dict(size=IFR_attribute["Minimum IFR"]*30, color="white",opacity=1),showlegend=False,hoverinfo='skip') 

#add subtitle 
fig.add_annotation(text="Hover over each marker to observe the variance of the IFR(%) indicated by the width of the ring",
                      xref="paper", yref="paper",
                      x=0.5, y=1.06,showarrow=False)  

#add title
fig.update_layout(
    title={
        'text': "COVID-19 Death (Infection Fatality) Rate of each country",
        'y':0.95,
        'x':0.5,
        'xanchor': 'center',
        'yanchor': 'top'})

#create white background
fig.update_layout(plot_bgcolor="white")

# update legend
fig.update_layout(
        legend=dict(
            x=0.8,
            y=0.05,
            bordercolor="Black",
            borderwidth=2
        )
    )

# add gridlines
fig.update_xaxes(showline=True, linewidth=2, linecolor='black', gridcolor='black')
fig.update_yaxes(showline=True, linewidth=2, linecolor='black', gridcolor='black')

# show figure
fig.show()

The first observation is the linear correlation betwen `gdp_per_capita`a and `human_development_index`. This is except as we say a linear relationship with both these attributes to the IFR. The next point is that they IFR, given by the size of the markers increase as a function of these two attributes where smaller IFR's such as for India are on the bottom left and and higher IFR's i.e. for Australia are at the top right. Finally, the width of the rings vary across the points and it is evident that the width of the marker for Australia and South Africa are thicker indicating a higher uncertainty.

The interactivity for this graph has been enabled allowing viewers to hover over the 'rings' and obtain the exact for the two attributes plus the minimum and maximum IFR. This feature also assists viewers with colour vision deficinecy and other viewers who struggle to comprehend graphs. 

For this graph, we simulated Blue Cone Monochromacy  which is a form of colour blindness where individuals a lower ability or inability to distinguish colours. 

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/blue-cone.JPG?token=AAABCWN5IFI4QOPSUB5MQXK7XW5QG)

All colours are still distinguishable.

The two visualisations seen so far have been continuously improved as they were used in the five **think alouds** that can be found here: https://github.sydney.edu.au/swan9801/R13B-Group4-COVID/blob/master/Process%20Notebooks/Code%20Review/THINK%20ALOUD.pdf




##### Visualisation Three: Map plot

Finally, we can visualise the IFR and uncertainties using a different approach. Both visualisations above illustrate these two values for different countries that are understood better by viewers who have the skills to read graphs. Considering the general public, a map plot plots the map of the earth and this can be utilised in showing the IFR and its uncertainties. 

The code below plots the world map with the IFR shaded as a continuous colour for the countries analysed. The interactive feature also includes the IFR with its respective uncertainty. 

In [60]:
# plot map of Earth with colour scheme representing the IFR
fig = px.choropleth(IFR_attribute, locations="iso_code",
                    color="IFR",
                    hover_name="location",
                   color_continuous_scale=px.colors.sequential.PuRd,
                   custom_data=["location","Minimum IFR","Maximum IFR"])

# update hover info
fig.update_traces(
    hovertemplate="<br>".join([
        "<b>%{customdata[0]}</b><br>",
        "IFR Range: %{customdata[1]:.2f}%-%{customdata[2]:.2f}%"
    ])
)

# add title
fig.update_layout(
        title={
            'text': "COVID-19 Death (Infection Fatality) Rate Around the World",
            'y':0.95,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top'})

# add subtitle
fig.add_annotation(text="Hover over each coloured country to obtain the IFR(%) and its variance",
                      xref="paper", yref="paper",
                      x=0.53, y=1.05,showarrow=False)

# show figure
fig.show()

The graph above colour codes the six countries analysed on a continuous spectrum indicating the IFR currently. It is evident that the death rate for Australia is the highest, indicated by the dark pink colour followed by the United States, Russia, Brazil, South Africa and India. The interactivity for this plot is enabled where viewers can hover over each country analysed and obtain the death rate as a range. This range is essentially the minimum and maximum IFR obtained for the previous visualisation. 


The colour gradient and interactivity accounts for viewers who are colour sensitive. As this form of visualisation is creative and requires very little to no graph interpretation skills, this graph appeals to viewers such as the general public. 

For this graph, we simulated Monochromacy/Achromatopsia which is a form of colour blindness where individuals a lower ability or inability to distinguish colours. 

![title](https://raw.github.sydney.edu.au/swan9801/R13B-Group4-COVID/master/ColourSimulator/mono.JPG?token=AAABCWP2ZR6E27T5MQK5P4C7XW5SM)

While there are no colours, the gradient of the greys with the help of the interactive hover feature assists viewers who are completely colour blind. 


## **C. Discussion**

*The author of this section is: Cynthia Mather*

*The editor of this section is: Sherry Wang*

*start 16-11-2020 end 18-11-2020*

### Australia's high death rate & biases

The Infection Fatality Rate was the most suitable method of calculating a death rate os a virus, which was achieved for six countries: Australia, Brazil, India, Russia, South Africa and the United States as it was more stable across time unlike the case fatality rate and was a true value as it considered the number of infection individuals both reported and unreported. As Australia has the highest IFR and India has the lowest IFR which has resulting the existance of *confirmation bias* within the team and in th think alouds. It is evident in the new cases figures during the EDA process illustrated india to have a higher number of deaths each day than Australia. However, when calculating the rate at which people were dying due to Covid, this rate was significantly higher for Australia indicating that a larger proportion of infected individuals are more likely to die from this virus than in India. From results like these and comparing the quality of life in both countries, confirmation bias exists such that we (including all five participants of the think-alouds) assumed that India would have a higher death rate to Australia. Recall confirmation bias is the tendency to pick out information that confirms our beliefs and this is evident here as everyone assume Australia to have a lower death rate than Australia. This assumption to some extent is acceptable as we say in the EDA section, the total cases and deaths in India was significantly higher than Australia such that the data in the non-log scale appear to be at zero but this relates back to anochoring bias. Recall *ancchoring bias* is a form of cognitive bias where individuals rely heavily on the first piece of information given and in this notebook, it would be the comparision between the number of confirmed cases and deaths between each country. However the key part to notice is that the IFR is calculated as the number of deaths over the number of infected people and since the number of infection individuals in Australia is low, this significantly increases the IFR. The popoulation proportion aged 65 years and older was a good indicator of how age is a risk factor of Covid such that for individuals with respirtory health conditions such as asthma, are generally in the high risk factor and this is generally associated with older individuals. With Australia having the highest proportion of indivduals aged 65 years and older, it is a potential confounding factor for the IFR and hence a higher ratio of people dying from the virus. Furthermore, the large confidence interval for Australia is potentially a result of less number of individuals with the virus and therefore less data to estimate. Recall that increasing a sample size decreases the variance, assuming the observations are independent identically distributed. 


#### Dealing with biases

When creating our visulisation results we took into consideration for potential *confirmation bias* for the data analyst and the target audience, as individuals tend have the perceptions that countries Australia and United States with a higher Human Development Index will have lower IFR, whereas countries such as India should have higher IFR or death rates. However, our exploration with the confounding factor `human_development_index` challenges the confirmation biases that the stakeholders might have. This addresses to the audience that there exist many underlying factors that impact the death rate of COVID and encourage people to careful consider evidence and uncertainties associated with the death rate of COVID. 

*Anchoring bias* is also accounted for by exploring different confounding factors with the IFR and creating visualisations in different ways without reaching a decision or conclusion immediately. As a team we also share perceptions by integrating different mental modesls, this allows the team when conducting data analysis not relying too much on the first few piece of information and draw conclusions but take into account of different perspectives.

### Limitations

One of the biggest limitations are the lack of uncertainties that are considered as they are difficult to quantify. These uncertainities for the death rate are the lower bound of the true errors as they only consider one form, the variance in the number of infected individuals that are reported and unreported. These uncertainites are therefore just a small contribution to the many that are not considered as they are difficult to quantify. Some other uncertainties include the following:

#### Uncertainty in data collection

One of the biggest influences in calculating mortality rates and comparing data from different countries is the method of data collection and the steps leading data from being observations to being recorded on a database as there are many confounding factors. As patient profiles such as age, sex, ethnicity etc. vary between countries which significantly increases the uncertainty as calculating a rate like above assumes all deaths were COVID-19 related and provides a generic rate. As this virus impacts the respiratory system, it severely impacts individuals with respiratory conditions such as asthma as well as older people. 

Another significant influencer of uncertainty is the definitions and testing strategies that vary across the world and over time. We saw that testing in each country was not constant over time, therefore calculating a single rate succumbs to a high uncertainties. With that in mind, the severity of this pandemic has changed over time and therefore its classification of mild/extreme cases has so too.


#### Uncertainty in presenting and calculating vs actual data

There are time lags in which data is made available from different databases. As this pandemic is ongoing, data is updated daily and at different times and therefore the same analysis conducted between my team and myself can differ purely based on when it was performed (the date and time).

There are also different methods of calculating mortality rates such as an infection fatality ratio (IFR) which estimates the proportion of deaths among all infected individuals. However, to eliminate bias around real-time data, we can calculate the Case Fatality ratio that calculates the proportion of individuals who contracted the virus and die from it to therefore measure the severity among the detected cases. There are different methods of calculating mortality rate and with the appropriate context and reasoning, these rates can vary.

While there are common methods for calculating mortality rates, there are scientific uncertainties that are introduced when results are stated. One example is rounding error in which results may satisfy each other due to rounding to an appropriate, small number of significant figures but in fact when written in longer formats, different by a small fraction. Furthermore, across different analysis and calculations, comparing values of different significant figures similarly results to a higher variance from the true value.


#### Uncertainty between different datasets
Many public datasets provide similar COVID-19 data such as the confirmed cases, deaths and recoveries. Sources for different countries come from health officials in their respective countries, however there are also worldwide sources such as Johns Hopkins. However, as many sources obtain data from each other, we would expect a small uncertainty between each data source used. Furthermore, as sources obtain and update their data at different times, this influence the analysis being run as on a particular, the cases may not be updated in one source but are in another and therefore it is difficult to compare.


#### Uncertainities in pre analytics

Finally, there is a lot of uncertainty in what happens before the data is reported. This includes how the cases were collected i.e. methods of testing and potential selection bias that arises as well as transparancy and health officials preserving the immutibility of the data. 



### Future Work

The biggest take away result from this notebook is the three different methods of visualising the Covid-19 death rate (IFR) and its uncertainties in six different countries that cater to different audiences. As a result of the death rates obtained has lead to a strong evidence of cognitive biases such as confirmation and anchoring bias and overconfidence as individals assumed 'well-off' countries like Australia had low death rates and India to have a higher death rate. This is evidently not that case but as results in the viewers assuming the data and analytics was wrong (participant 2 of the think aloud) and therefore question the integrity of the results, despite during data analsis the team tried to address the biases. Therefore, further analysis and statistical testing, hypothesising and modelling is required to understand if these results are statistically significant and therefore mitigate the biases observed by presenting more evidence for these results. 